In [1]:
'''
Author: error: error: git config user.name & please set dead value or install git && error: git config user.email & please set dead value or install git & please set dead value or install git
Date: 2023-10-28 11:56:40
LastEditors: error: error: git config user.name & please set dead value or install git && error: git config user.email & please set dead value or install git & please set dead value or install git
LastEditTime: 2023-10-28 12:34:14
FilePath: /backtest-strategies/strategy/quick_scalpingV2.ipynb
Description: 这是默认设置,请设置`customMade`, 打开koroFileHeader查看配置 进行设置: https://github.com/OBKoro1/koro1FileHeader/wiki/%E9%85%8D%E7%BD%AE
'''
import pandas as pd
import numpy as np

INIT_CASH = 100
path = '../data/APTUSDT_5m.csv'
symbol = path.split('/')[-1].split('_')[0].replace('USDT', '')
df = pd.read_csv(path)
df.head()

time   open   high    low  close   volume
0  2023-08-20 00:00:00  6.013  6.032  6.010  6.031  52755.0
1  2023-08-20 00:05:00  6.031  6.032  6.022  6.028  32024.5
2  2023-08-20 00:10:00  6.028  6.039  6.024  6.034  40720.3
3  2023-08-20 00:15:00  6.035  6.050  6.035  6.045  48565.2
4  2023-08-20 00:20:00  6.044  6.052  6.038  6.051  43775.2

In [2]:
import pandas_ta as ta

temp = df.ta.macd()
df['MACD'] = temp['MACD_12_26_9']   
df['MACD_SIGNAL'] = temp['MACDs_12_26_9']
df['MACD_HIST'] = temp['MACDh_12_26_9']
temp = df.ta.cdl_pattern(name="longline")
df['LONG_LINE'] = temp['CDL_LONGLINE']
#buy LONG_LINE == 100 and MACD_HIST > 0
df['Signal_Buy'] = np.where((df['LONG_LINE'] == 100) & (df['MACD_HIST'] > 0), 2, 0)
#sell LONG_LINE == -100 and MACD_HIST < 0
df['Signal_Sell'] = np.where((df['LONG_LINE'] == -100) & (df['MACD_HIST'] < 0), 1, 0)
df['Signal'] = df['Signal_Buy'] + df['Signal_Sell']
df['ATR'] = df.ta.atr()
df['ADX'] = df.ta.adx()['ADX_14']
#help(ta.adx)

In [3]:
df.ta.cdl_pattern(name="longline").value_counts()

CDL_LONGLINE
 0.0            15617
 100.0           2056
-100.0           1827
dtype: int64

In [4]:
help(ta.mad)

Help on function mad in module pandas_ta.statistics.mad:

mad(close, length=None, offset=None, **kwargs)
    Rolling Mean Absolute Deviation
    
    Sources:
    
    Calculation:
        Default Inputs:
            length=30
        mad = close.rolling(length).mad()
    
    Args:
        close (pd.Series): Series of 'close's
        length (int): It's period. Default: 30
        offset (int): How many periods to offset the result. Default: 0
    
    Kwargs:
        fillna (value, optional): pd.DataFrame.fillna(value)
        fill_method (value, optional): Type of fill method
    
    Returns:
        pd.Series: New feature generated.



In [5]:
#dropna
df = df.dropna()
df.head()

time   open   high    low  close   volume      MACD  \
33  2023-08-20 02:45:00  6.030  6.031  6.023  6.027   8129.6 -0.002885   
34  2023-08-20 02:50:00  6.026  6.027  6.021  6.024   7456.4 -0.003019   
35  2023-08-20 02:55:00  6.024  6.028  6.018  6.019  21353.9 -0.003488   
36  2023-08-20 03:00:00  6.018  6.020  6.011  6.013  45307.6 -0.004295   
37  2023-08-20 03:05:00  6.013  6.018  6.010  6.012  14458.3 -0.004958   

    MACD_SIGNAL  MACD_HIST  LONG_LINE  Signal_Buy  Signal_Sell  Signal  \
33    -0.003700   0.000815        0.0           0            0       0   
34    -0.003564   0.000545        0.0           0            0       0   
35    -0.003549   0.000060        0.0           0            0       0   
36    -0.003698  -0.000597     -100.0           0            1       1   
37    -0.003950  -0.001008        0.0           0            0       0   

         ATR        ADX  
33  0.010731   9.448751  
34  0.010393   8.657512  
35  0.010365   8.462976  
36  0.010267   9.327601  
37  0.010105  10.239079

In [6]:
#set time to index

df['time'] = pd.to_datetime(df['time'])
df = df.set_index('time')
df.head()

/tmp/ipykernel_74143/1852176384.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['time'] = pd.to_datetime(df['time'])


open   high    low  close   volume      MACD  \
time                                                                 
2023-08-20 02:45:00  6.030  6.031  6.023  6.027   8129.6 -0.002885   
2023-08-20 02:50:00  6.026  6.027  6.021  6.024   7456.4 -0.003019   
2023-08-20 02:55:00  6.024  6.028  6.018  6.019  21353.9 -0.003488   
2023-08-20 03:00:00  6.018  6.020  6.011  6.013  45307.6 -0.004295   
2023-08-20 03:05:00  6.013  6.018  6.010  6.012  14458.3 -0.004958   

                     MACD_SIGNAL  MACD_HIST  LONG_LINE  Signal_Buy  \
time                                                                 
2023-08-20 02:45:00    -0.003700   0.000815        0.0           0   
2023-08-20 02:50:00    -0.003564   0.000545        0.0           0   
2023-08-20 02:55:00    -0.003549   0.000060        0.0           0   
2023-08-20 03:00:00    -0.003698  -0.000597     -100.0           0   
2023-08-20 03:05:00    -0.003950  -0.001008        0.0           0   

                     Signal_Sell  Signal       ATR        ADX  
time                                                           
2023-08-20 02:45:00            0       0  0.010731   9.448751  
2023-08-20 02:50:00            0       0  0.010393   8.657512  
2023-08-20 02:55:00            0       0  0.010365   8.462976  
2023-08-20 03:00:00            1       1  0.010267   9.327601  
2023-08-20 03:05:00            0       0  0.010105  10.239079

In [7]:
#rename columns
df.rename(columns={'open': 'Open', 'high': 'High', 'low': 'Low', 'close': 'Close', 'volume': 'Volume'}, inplace=True)

In [8]:
df['Signal'].value_counts()

0    17263
2     1159
1     1045
Name: Signal, dtype: int64

In [9]:
from backtesting import Strategy
from backtesting import Backtest

def SIGNAL(df,col_name):
    return df[col_name]

class Scalping_Strategy(Strategy):
    atr_sl_rate = 1.3
    TPSL_rate = 1.5
    save_size_rate = 0.125
    init_cash = INIT_CASH
    profit_target = 500
    size_multiplier_rate = 0.5

    def init(self):
        super().init()
        self.signal = self.I(SIGNAL, self.data, 'Signal')

    def next(self):
        super().next()

        slatr = self.atr_sl_rate * self.data.ATR[-1]
        size_multiplier = self.size_multiplier_rate if self.equity >= self.profit_target else 1.0

        if self.signal == 2:
            sl_price = self.data.Close[-1] - slatr
            tp_price = self.data.Close[-1] + self.TPSL_rate * slatr
            size = min(self.save_size_rate * self.equity / slatr, self.init_cash / slatr) * size_multiplier
            if self.equity > self.init_cash * 1.5:
                self.buy(sl=sl_price, tp=tp_price, size=int(size))
            else:
                self.buy(sl=sl_price, tp=tp_price)

        if self.signal == 1:
            sl_price = self.data.Close[-1] + slatr
            tp_price = self.data.Close[-1] - self.TPSL_rate * slatr
            size = min(self.save_size_rate * self.equity / slatr, self.init_cash / slatr) * size_multiplier
            if self.equity >= self.init_cash * 1.5:
                self.sell(sl=sl_price, tp=tp_price, size=int(size))
            else:
                self.sell(sl=sl_price, tp=tp_price)
            

bt = Backtest(df, Scalping_Strategy, cash=INIT_CASH, commission=.00002, margin=.05)
stat = bt.run()
stat

Start                     2023-08-20 02:45:00
End                       2023-10-26 16:55:00
Duration                     67 days 14:10:00
Exposure Time [%]                   44.316022
Equity Final [$]                     1.541332
Equity Peak [$]                    173.611839
Return [%]                         -98.458668
Buy & Hold Return [%]                5.939937
Return (Ann.) [%]                      -100.0
Volatility (Ann.) [%]         11470081.912554
Sharpe Ratio                              0.0
Sortino Ratio                             0.0
Calmar Ratio                              0.0
Max. Drawdown [%]                    -99.5963
Avg. Drawdown [%]                  -13.508176
Max. Drawdown Duration       64 days 22:20:00
Avg. Drawdown Duration        5 days 01:52:00
# Trades                                 1460
Win Rate [%]                         42.60274
Best Trade [%]                       1.902192
Worst Trade [%]                     -1.726537
Avg. Trade [%]                    

In [10]:
import plotly.graph_objects as go

fig = go.Figure(data=[go.Scatter(x=stat['_equity_curve'].index, y=stat['_equity_curve']['Equity'])])
fig.add_trace(go.Scatter(x=stat['_equity_curve'].index, y=[INIT_CASH]*len(stat['_equity_curve'].index), name='Initial Cash'))
fig.show()

In [11]:
%%time
stats = bt.optimize(atr_sl_rate = np.arange(0.3, 2.6, 0.2).tolist(),
                    TPSL_rate = np.arange(0.3, 2.6, 0.2).tolist(),
                    size_multiplier_rate = np.arange(0.1, 0.5, 0.1).tolist(),
                    maximize='Equity Final [$]')
stats

/home/hibana2077/.local/lib/python3.10/site-packages/backtesting/backtesting.py:1488: UserWarning:

Searching for best of 576 configurations.



Backtest.optimize:   0%|          | 0/12 [00:00<?, ?it/s]

CPU times: user 829 ms, sys: 120 ms, total: 949 ms
Wall time: 1min 2s


Start                     2023-08-20 02:45:00
End                       2023-10-26 16:55:00
Duration                     67 days 14:10:00
Exposure Time [%]                   30.780295
Equity Final [$]                   174.458405
Equity Peak [$]                    320.755958
Return [%]                          74.458405
Buy & Hold Return [%]                5.939937
Return (Ann.) [%]                  880.144456
Volatility (Ann.) [%]        4615093052.87979
Sharpe Ratio                              0.0
Sortino Ratio                        2.668975
Calmar Ratio                         9.082447
Max. Drawdown [%]                  -96.906092
Avg. Drawdown [%]                  -18.618111
Max. Drawdown Duration       34 days 21:10:00
Avg. Drawdown Duration        2 days 13:17:00
# Trades                                  812
Win Rate [%]                        50.492611
Best Trade [%]                       1.826278
Worst Trade [%]                     -2.257163
Avg. Trade [%]                    

In [12]:
stats.keys()

Index(['Start', 'End', 'Duration', 'Exposure Time [%]', 'Equity Final [$]',
       'Equity Peak [$]', 'Return [%]', 'Buy & Hold Return [%]',
       'Return (Ann.) [%]', 'Volatility (Ann.) [%]', 'Sharpe Ratio',
       'Sortino Ratio', 'Calmar Ratio', 'Max. Drawdown [%]',
       'Avg. Drawdown [%]', 'Max. Drawdown Duration', 'Avg. Drawdown Duration',
       '# Trades', 'Win Rate [%]', 'Best Trade [%]', 'Worst Trade [%]',
       'Avg. Trade [%]', 'Max. Trade Duration', 'Avg. Trade Duration',
       'Profit Factor', 'Expectancy [%]', 'SQN', '_strategy', '_equity_curve',
       '_trades'],
      dtype='object')

In [13]:
stats._strategy

<Strategy Scalping_Strategy(atr_sl_rate=1.7000000000000002,TPSL_rate=1.1,size_multiplier_rate=0.1)>

In [14]:
import plotly.graph_objects as go

fig = go.Figure(data=[go.Scatter(x=stats['_equity_curve'].index, y=stats['_equity_curve']['Equity'],name='Equity')])
#add a initial cash line
fig.add_trace(go.Scatter(x=stats['_equity_curve'].index, y=[INIT_CASH]*len(stats['_equity_curve'].index), name='Initial Cash'))
fig.update_layout(title='Profit |'+symbol, yaxis_title='USDT', xaxis_title='Date')
fig.show()